## 3.5 Topic Modeling

To better understand the differences in communication of politicians on Twitter and in the Bundestag, we perform a topic modeling. For this we test three different approaches, before we choose the best performing as our final model. We apply hyperparameter tuning if applicable but omit classic train test split validation. We are gonna analyse the validity of the topic model in the Results section.

In [1]:
import pickle
from pprint import pprint
from imp import reload
from operator import itemgetter
from datetime import datetime
import os
os.environ["TOKENIZERS_PARALLELISM"] = "false"

import numpy as np
import pandas as pd

import gensim
import gensim.corpora as corpora
from gensim.utils import simple_preprocess
from gensim.models import CoherenceModel, LdaMulticore
from gensim.models.nmf import Nmf

import pyLDAvis
import pyLDAvis.gensim_models
pyLDAvis.enable_notebook()

from bertopic import BERTopic

from tqdm.notebook import tqdm
tqdm.pandas()

/Users/jakob/opt/miniconda3/envs/amca/lib/python3.8/site-packages/plotly/graph_objs/__init__.py:287: DeprecationWarning: distutils Version classes are deprecated. Use packaging.version instead.
  if LooseVersion(ipywidgets.__version__) >= LooseVersion("7.0.0"):
/Users/jakob/opt/miniconda3/envs/amca/lib/python3.8/site-packages/plotly/graph_objs/__init__.py:287: DeprecationWarning: distutils Version classes are deprecated. Use packaging.version instead.
  if LooseVersion(ipywidgets.__version__) >= LooseVersion("7.0.0"):
/Users/jakob/opt/miniconda3/envs/amca/lib/python3.8/site-packages/plotly/graph_objs/__init__.py:287: DeprecationWarning: distutils Version classes are deprecated. Use packaging.version instead.
  if LooseVersion(ipywidgets.__version__) >= LooseVersion("7.0.0"):
/Users/jakob/opt/miniconda3/envs/amca/lib/python3.8/site-packages/plotly/graph_objs/__init__.py:287: DeprecationWarning: distutils Version classes are deprecated. Use packaging.version instead.
  if LooseVersion(ip

### 3.5.1 Latent Dirichlet Allocation

Latent Dirichlet Allocation (LDA) constitutes a state of the art approach [Citaiton needed https://journalofbigdata.springeropen.com/track/pdf/10.1186/s40537-019-0255-7.pdf)] for topic modeling. LDA is a unsupervised machine learning technique that uses generative statistical models to extract topics from a collection of documents [citation needed]. Based on the underlying model it assigns a probability distribution over the vocabulary of the documents to topics that can be used for the topic detection. We will base our choice of the optimal hyperparameter combination on the coherence of the resulting topic model. This decision is based on the discussion [here](http://topicmodels.info/ckling/tmt/part4.pdf) and [here](https://dl.acm.org/doi/abs/10.1145/2684822.2685324). 

#### Define hyperparameters for optimization.

We optimize the hyperparameters of the LDA model based on a grid search with the variables topic number (k), the a-priory belief of document-topic distribution (alpha) and the the a-priory  belief of topic-word distribution (eta) [citation of https://radimrehurek.com/gensim/models/ldamodel.html]. This hyperparemter optimization is loosely based on this [article](https://towardsdatascience.com/evaluate-topic-model-in-python-latent-dirichlet-allocation-lda-7d57484bb5d0).

In [2]:
# Topics range
min_topics = 10
max_topics = 150
step_size = 10
topics_range = range(min_topics, max_topics, step_size)

In [3]:
# Alpha parameter
alpha = list(np.arange(0.01, 1, 0.3)) #
alpha.append('symmetric')
alpha.append('asymmetric')

In [4]:
# Beta parameter
beta = list(np.arange(0.01, 1, 0.3))
beta.append('symmetric')

In [5]:
# Function for calculating coherence values of specific hyperparamter combinations
def compute_lda_coherence_values(corpus, text, id2word, k, a, b):
    lda_model = LdaMulticore(corpus=corpus,
                             id2word=id2word,
                             num_topics=k, 
                             random_state=42,
                             alpha=a,
                             eta=b)
    coherence_model_lda = CoherenceModel(model=lda_model, texts=text, dictionary=id2word, coherence='c_v')
    return coherence_model_lda.get_coherence()

In [6]:
# Function for executing a hyperparameter optimization
def hyperparameter_lda(data_preprocessed, title, topics_range, alpha, beta):
    id2word = corpora.Dictionary(data_preprocessed.text_preprocessed.to_list())
    # These hyperparameter could also be trialed in an extend scope
    id2word.filter_extremes(no_below=10, no_above=0.1)
    texts = data_preprocessed.text_preprocessed.to_list()
    corpus = [id2word.doc2bow(text) for text in texts]
    model_results = {'Topics': [],
                     'Alpha': [],
                     'Beta': [],
                     'Coherence': []
                    }
    grid = {}
    grid['Validation_Set'] = {}
    for k in tqdm(topics_range):
        print("Number of topics:" + str(k))
        for a in tqdm(alpha):
            print("Alpha value:" + str(a))
            for b in tqdm(beta):
                print("Beta value:" + str(b))
                cv = compute_lda_coherence_values(corpus=corpus,text = texts,
                                              id2word=id2word, k=k, a=a, b=b)
                model_results['Topics'].append(k)
                model_results['Alpha'].append(a)
                model_results['Beta'].append(b)
                model_results['Coherence'].append(cv)
    results_df = pd.DataFrame(model_results)
    results_df.to_csv('../data/processed/lda_tuning_results_' + title + '.csv', index=False)
    return results_df

#### 3.5.1.1 Hyperparameter optimization LDA for tweets

In [7]:
# Load data
tweets_processed_lda = pickle.load(open( "../data/processed/tweets_processed.p", "rb" ))

In [8]:
# Hyperparameter optimization
# Uncomment if you want to repeat the hyperparameter optimization
# hyperparameter_lda_tweets = hyperparameter_lda(tweets_processed_lda, "tweets", topics_range, alpha, beta)

In [9]:
# Save hyperparameter
# Uncomment if you want to repeat the hyperparameter optimization
# hyperparameter_lda_tweets.to_csv('../data/processed/lda_tuning_results_tweets.csv', index = False)

#### 3.5.1.2 Calculate best model LDA for tweets

In [10]:
# Load data
lda_tuning_results_tweets = pd.read_csv('../data/processed/lda_tuning_results_tweets.csv')

In [11]:
# Prepare corpus
id2word_tweets_lda = corpora.Dictionary(tweets_processed_lda.text_preprocessed.to_list())
id2word_tweets_lda.filter_extremes(no_below=5, no_above=0.1)
texts_tweets_lda = tweets_processed_lda.text_preprocessed.to_list()
corpus_tweets_lda = [id2word_tweets_lda.doc2bow(text) for text in texts_tweets_lda]

In [12]:
k_optimal_lda_tweets = int(lda_tuning_results_tweets.sort_values("Coherence", ascending = False).reset_index(drop = True).Topics[0])
try:
    a_optimal_lda_tweets = float(lda_tuning_results_tweets.sort_values("Coherence", ascending = False).reset_index(drop = True).Alpha[0])
except ValueError:
    a_optimal_lda_tweets = lda_tuning_results_tweets.sort_values("Coherence", ascending = False).reset_index(drop = True).Alpha[0]
try:
    b_optimal_lda_tweets = float(lda_tuning_results_tweets.sort_values("Coherence", ascending = False).reset_index(drop = True).Beta[0])
except ValueError:
    b_optimal_lda_tweets = lda_tuning_results_tweets.sort_values("Coherence", ascending = False).reset_index(drop = True).Beta[0]

In [13]:
# Train model
lda_model_tweets = LdaMulticore(corpus=corpus_tweets_lda,
                                 id2word=id2word_tweets_lda,
                                 num_topics=k_optimal_lda_tweets,
                                 random_state=42,
                                 alpha=a_optimal_lda_tweets,
                                 eta=b_optimal_lda_tweets)

In [14]:
# Calculate final coherence value
coherence_model_lda_tweets = CoherenceModel(model=lda_model_tweets, texts=texts_tweets_lda, dictionary=id2word_tweets_lda, coherence='c_v')
coherence_lda_tweets = coherence_model_lda_tweets.get_coherence()
print("The final model coherence of the LDA for Tweets is: " + str(round(coherence_lda_tweets,2)))

The final model coherence of the LDA for Tweets is: 0.54


In [15]:
# Visually inspect result
lda_vis_tweets = pyLDAvis.gensim_models.prepare(lda_model_tweets, corpus_tweets_lda, id2word_tweets_lda)
lda_vis_tweets

PreparedData(topic_coordinates=              x         y  topics  cluster       Freq
topic                                                
0      0.274350 -0.011194       1        1  15.861445
1      0.267469  0.006294       2        1  12.730461
2      0.237134 -0.017200       3        1   9.235930
3      0.218591 -0.043451       4        1   7.732944
4      0.209445  0.015472       5        1   6.689900
...         ...       ...     ...      ...        ...
88    -0.034209  0.000210      96        1   0.117404
92    -0.036342 -0.000717      97        1   0.108084
91    -0.047947  0.002919      98        1   0.107413
90    -0.037570 -0.003165      99        1   0.104460
94    -0.042539 -0.000362     100        1   0.086599

[100 rows x 5 columns], topic_info=              Term         Freq        Total  Category  logprob  loglift
1275           afd  8116.000000  8116.000000   Default  30.0000  30.0000
482    glückwunsch  1060.000000  1060.000000   Default  29.0000  29.0000
483      herzliche   732.000000   732.000000   Default  28.0000  28.0000
11396         gera   664.000000   664.000000   Default  27.0000  27.0000
254         berlin  3463.000000  3463.000000   Default  26.0000  26.0000
...            ...          ...          ...       ...      ...      ...
13971           tb     0.285782   235.781941  Topic100  -8.2696   0.3362
928         wählen     0.318071  1444.461187  Topic100  -8.1626  -1.3693
914            cdu     0.322191  3362.907251  Topic100  -8.1497  -2.2015
1398    eigentlich     0.307753  1708.684245  Topic100  -8.1956  -1.5703
345         setzen     0.305110  1389.682102  Topic100  -8.2042  -1.3723

[4551 rows x 6 columns], token_table=      Topic      Freq   Term
term                        
6499      1  0.045841     aa
6499      2  0.045841     aa
6499      3  0.045841     aa
6499      4  0.137522     aa
6499      5  0.045841     aa
...     ...       ...    ...
4564      4  0.043032  şahin
4564      5  0.043032  şahin
4564      6  0.043032  şahin
4564      7  0.043032  şahin
4564     67  0.043032  şahin

[50803 rows x 3 columns], R=30, lambda_step=0.01, plot_opts={'xlab': 'PC1', 'ylab': 'PC2'}, topic_order=[1, 2, 3, 4, 5, 6, 7, 8, 9, 10, 13, 11, 12, 18, 14, 23, 15, 34, 16, 29, 17, 21, 20, 26, 19, 31, 50, 40, 24, 22, 32, 30, 27, 28, 38, 36, 42, 55, 33, 59, 39, 25, 43, 74, 61, 64, 45, 37, 62, 68, 35, 41, 46, 51, 53, 44, 82, 69, 48, 54, 73, 49, 99, 66, 77, 57, 97, 63, 98, 79, 47, 75, 65, 67, 71, 88, 96, 84, 52, 56, 76, 94, 72, 78, 100, 58, 70, 80, 85, 86, 81, 90, 87, 83, 60, 89, 93, 92, 91, 95])

#### 3.5.1.3 Hyperparameter optimization LDA for speeches

In [16]:
# Load data
speeches_processed_lda = pickle.load(open( "../data/processed/speeches_processed.p", "rb" ))

In [17]:
# Hyperparameter optimization
# Uncomment if you want to repeat the hyperparameter optimization
# hyperparameter_lda_speeches = hyperparameter_lda(speeches_processed_lda, "tweets", topics_range, alpha, beta)

In [18]:
# Save hyperparameter
# Uncomment if you want to repeat the hyperparameter optimization
# hyperparameter_lda_speeches.to_csv('../data/processed/lda_tuning_results_speeches.csv', index = False)

#### 3.5.1.4 Calculate best model LDA for speeches

In [19]:
# Load data
lda_tuning_results_speeches = pd.read_csv('../data/processed/lda_tuning_results_speeches.csv')

In [20]:
# Prepare corpus
id2word_speeches_lda = corpora.Dictionary(tweets_processed_lda.text_preprocessed.to_list())
id2word_speeches_lda.filter_extremes(no_below=5, no_above=0.1)
texts_speeches_lda = tweets_processed_lda.text_preprocessed.to_list()
corpus_speeches_lda = [id2word_speeches_lda.doc2bow(text) for text in texts_speeches_lda]

In [21]:
k_optimal_lda_speeches = int(lda_tuning_results_speeches.sort_values("Coherence", ascending = False).reset_index(drop = True).Topics[0])
try:
    a_optimal_lda_speeches = float(lda_tuning_results_speeches.sort_values("Coherence", ascending = False).reset_index(drop = True).Alpha[0])
except ValueError:
    a_optimal_lda_speeches = lda_tuning_results_speeches.sort_values("Coherence", ascending = False).reset_index(drop = True).Alpha[0]
try:
    b_optimal_lda_speeches = float(lda_tuning_results_speeches.sort_values("Coherence", ascending = False).reset_index(drop = True).Beta[0])
except ValueError:
    b_optimal_lda_speeches = lda_tuning_results_speeches.sort_values("Coherence", ascending = False).reset_index(drop = True).Beta[0]

In [22]:
# Train model
lda_model_speeches = LdaMulticore(corpus=corpus_speeches_lda,
                                 id2word=id2word_speeches_lda,
                                 num_topics=k_optimal_lda_speeches,
                                 random_state=42,
                                 alpha=a_optimal_lda_speeches,
                                 eta=b_optimal_lda_speeches)

In [23]:
# Calculate final coherence value
coherence_model_lda_speeches = CoherenceModel(model=lda_model_speeches, texts=texts_speeches_lda, dictionary=id2word_speeches_lda,
                                                    coherence='c_v')
coherence_lda_speeches = coherence_model_lda_speeches.get_coherence()
print("The final model coherence of the LDA for Speeches is: " + str(round(coherence_lda_speeches,2)))

The final model coherence of the LDA for Speeches is: 0.37


In [24]:
# Visually inspect result
lda_vis_speeches = pyLDAvis.gensim_models.prepare(lda_model_speeches, corpus_speeches_lda, id2word_speeches_lda)
lda_vis_speeches

PreparedData(topic_coordinates=              x         y  topics  cluster      Freq
topic                                               
0      0.120816 -0.023357       1        1  2.260270
1      0.118426 -0.025104       2        1  2.034889
70    -0.090188 -0.090630       3        1  1.681558
2      0.110601 -0.018491       4        1  1.645849
3      0.107114 -0.010038       5        1  1.600015
...         ...       ...     ...      ...       ...
31     0.006295  0.015706      76        1  1.072598
28     0.040192 -0.005486      77        1  1.052836
50    -0.014259 -0.014235      78        1  1.049251
54    -0.042581 -0.000926      79        1  1.045569
25     0.021997 -0.041267      80        1  1.032896

[80 rows x 5 columns], topic_info=              Term          Freq         Total Category  logprob  loglift
9827      brandner   2108.000000   2108.000000  Default  30.0000  30.0000
11396         gera   1228.000000   1228.000000  Default  29.0000  29.0000
482    glückwunsch   1938.000000   1938.000000  Default  28.0000  28.0000
1733           via   1303.000000   1303.000000  Default  27.0000  27.0000
1275           afd  10045.000000  10045.000000  Default  26.0000  26.0000
...            ...           ...           ...      ...      ...      ...
254         berlin     66.039180   4307.419471  Topic80  -5.3057   0.3950
1275           afd     68.522809  10045.901828  Topic80  -5.2688  -0.4150
742      regierung     58.909310   1880.281749  Topic80  -5.4200   1.1096
38          mensch     64.492709   6857.078594  Topic80  -5.3294  -0.0937
1343         groko     57.442092   2205.815493  Topic80  -5.4452   0.9247

[5592 rows x 6 columns], token_table=       Topic      Freq     Term
term                           
6106       2  0.025222   aachen
6106      11  0.151330   aachen
6106      70  0.807092   aachen
11339      2  0.049018  abbruch
11339     11  0.024509  abbruch
...      ...       ...      ...
10102     66  0.021041   üblich
10102     67  0.007014   üblich
10742      1  0.038306    üppig
10742     26  0.919342    üppig
947       36  0.960873   şimşek

[45662 rows x 3 columns], R=30, lambda_step=0.01, plot_opts={'xlab': 'PC1', 'ylab': 'PC2'}, topic_order=[1, 2, 71, 3, 4, 63, 54, 27, 44, 78, 5, 73, 6, 39, 12, 24, 34, 22, 48, 16, 8, 46, 9, 7, 23, 43, 30, 68, 35, 65, 42, 77, 31, 57, 61, 50, 37, 60, 53, 38, 40, 76, 64, 41, 79, 52, 33, 56, 67, 15, 25, 13, 66, 80, 47, 10, 74, 69, 19, 14, 62, 59, 70, 58, 18, 45, 21, 36, 49, 17, 20, 75, 28, 11, 72, 32, 29, 51, 55, 26])

### 3.5.2 Non Negative Matrix Factorization

Another approach for topic modeling we are testing is Non Negative Matrix Factorization (NNMF). This technique is another unsupervised machine learning method, that factorizes a matrix into two matrices, that give a less complex representation of the the original matrix. In our case we use it for creating a document-term matrix, that help to identify topics of the considered documents.

#### Define hyperparameters for optimization.

We optimize the hyperparameters of the NNMF model based on a grid search with the variables topic number (k).

In [25]:
# Function for calculating coherence values of specific hyperparamter combinations
def compute_nnmf_coherence_values(corpus, text, id2word, k):
    nmf_model = Nmf(
        corpus=corpus,
        id2word=id2word,
        num_topics=k,
        random_state=42
    )
    coherence_model_lda = CoherenceModel(model=nmf_model, texts=text, dictionary=id2word, coherence='c_v')
    return coherence_model_lda.get_coherence()

In [26]:
# Function for executing a hyperparameter optimization
def hyperparameter_nnmf(data_preprocessed, title, topics_range):
    id2word = corpora.Dictionary(data_preprocessed.text_preprocessed.to_list())
    id2word.filter_extremes(no_below=10, no_above=0.1)
    texts = data_preprocessed.text_preprocessed.to_list()
    corpus = [id2word.doc2bow(text) for text in texts]
    model_results = {'Topics': [],
                     'Coherence': []
                    }
    grid = {}
    grid['Validation_Set'] = {}
    for k in tqdm(topics_range):
        print("Number of topics:" + str(k))
        cv = compute_nnmf_coherence_values(corpus=corpus,text = texts,
                                      id2word=id2word, k=k)
        model_results['Topics'].append(k)
        model_results['Coherence'].append(cv)
    results_df = pd.DataFrame(model_results)
    results_df.to_csv('../data/processed/nnmf_tuning_results_' + title + '.csv', index=False)
    return results_df

#### 3.5.2.1 Hyperparameter optimization NNMF for tweets

In [27]:
# Load data
tweets_processed_nnmf = pickle.load(open("../data/processed/tweets_processed.p", "rb" ))

In [28]:
# Hyperparameter optimization
# Uncomment if you want to repeat the hyperparameter optimization
# hyperparameter_nnmf_tweets = hyperparameter_nnmf(tweets_processed_nnmf, "tweets", topics_range)

In [29]:
# Save hyperparameter
# Uncomment if you want to repeat the hyperparameter optimization
# hyperparameter_nnmf_tweets.to_csv('../data/processed/nnmf_tuning_results_tweets.csv', index = False)

#### 3.5.2.2 Calculate best model NNMF for tweets

In [30]:
# Load data
tweets_processed_nnmf = pickle.load(open( "../data/processed/tweets_processed.p", "rb" ))
nnmf_tuning_results_tweets = pd.read_csv('../data/processed/nnmf_tuning_results_tweets.csv')

In [31]:
# Prepare corpus
id2word_tweets_nnmf = corpora.Dictionary(tweets_processed_nnmf.text_preprocessed.to_list())
id2word_tweets_nnmf.filter_extremes(no_below=5, no_above=0.1)
texts_tweets_nnmf = tweets_processed_nnmf.text_preprocessed.to_list()
corpus_tweets_nnmf = [id2word_tweets_nnmf.doc2bow(text) for text in texts_tweets_nnmf]

In [32]:
k_optimal_nnmf_tweets = int(lda_tuning_results_tweets.sort_values("Coherence", ascending = False).reset_index(drop = True).Topics[0])

In [33]:
# Train model
nnmf_model_tweets = Nmf(corpus=corpus_tweets_nnmf,
                                 id2word=id2word_tweets_nnmf,
                                 num_topics=k_optimal_nnmf_tweets,
                                 random_state=42)

In [34]:
# Calculate final coherence value
coherence_model_nnmf_tweets = CoherenceModel(model=nnmf_model_tweets, texts=texts_tweets_nnmf, dictionary=id2word_tweets_nnmf,
                                                    coherence='c_v')
coherence_nnmf_tweets = coherence_model_nnmf_tweets.get_coherence()
print("The final model coherence of the NNMF for tweets is: " + str(round(coherence_nnmf_tweets,2)))

The final model coherence of the NNMF for tweets is: 0.33


In [35]:
# Visually inspect result
nnmf_model_tweets.show_topics()

[(33,
  '0.121*"deutsch" + 0.055*"treffen" + 0.017*"erklären" + 0.014*"absolut" + 0.009*"schutz" + 0.008*"kennen" + 0.005*"unternehmen" + 0.005*"geschichte" + 0.004*"person" + 0.004*"fragen"'),
 (32,
  '0.302*"mal" + 0.009*"schauen" + 0.008*"lesen" + 0.006*"schau" + 0.004*"sagen" + 0.004*"rein" + 0.004*"reden" + 0.004*"ne" + 0.003*"fragen" + 0.003*"eigentlich"'),
 (84,
  '0.081*"handeln" + 0.075*"herr" + 0.048*"verantwortung" + 0.023*"tragen" + 0.020*"grund" + 0.013*"sache" + 0.011*"übernehmen" + 0.009*"sichern" + 0.007*"treffen" + 0.006*"alt"'),
 (99,
  '0.066*"schritt" + 0.064*"gesetz" + 0.037*"polizei" + 0.036*"politische" + 0.013*"stimmen" + 0.011*"richtung" + 0.011*"ändern" + 0.008*"mitarbeiter" + 0.008*"richtige" + 0.007*"konzept"'),
 (19,
  '0.311*"deutschland" + 0.005*"frankreich" + 0.005*"million" + 0.003*"verantwortung" + 0.003*"jude" + 0.003*"zahl" + 0.003*"groß" + 0.003*"weltweit" + 0.003*"jüdisch" + 0.003*"armut"'),
 (34,
  '0.193*"diskutieren" + 0.014*"welt" + 0.013*"wähl

#### 3.5.2.3 Hyperparameter optimization NNMF for speeches

In [36]:
# Load data
speeches_processed_nnmf = pickle.load(open( "../data/processed/speeches_processed.p", "rb" ))

In [37]:
# Hyperparameter optimization
# Uncomment if you want to repeat the hyperparameter optimization
# hyperparameter_nnmf_speeches = hyperparameter_lda(speeches_processed_nnmf, "tweets", topics_range, alpha, beta)

In [38]:
# Save hyperparameter
# Uncomment if you want to repeat the hyperparameter optimization
# hyperparameter_nnmf_speeches.to_csv('../data/processed/nnmf_tuning_results_speeches.csv', index = False)

#### 3.5.2.4 Calculate best model NNMF for speeches

In [39]:
# Load data
speeches_processed_nnmf = pickle.load(open( "../data/processed/speeches_processed.p", "rb" ))
nnmf_tuning_results_speeches = pd.read_csv('../data/processed/nnmf_tuning_results_speeches.csv')

In [40]:
# Prepare corpus
id2word_speeches_nnmf = corpora.Dictionary(tweets_processed_nnmf.text_preprocessed.to_list())
id2word_speeches_nnmf.filter_extremes(no_below=5, no_above=0.1)
texts_speeches_nnmf = tweets_processed_nnmf.text_preprocessed.to_list()
corpus_speeches_nnmf = [id2word_speeches_nnmf.doc2bow(text) for text in texts_speeches_nnmf]

In [41]:
k_optimal_nnmf_speeches = int(lda_tuning_results_speeches.sort_values("Coherence", ascending = False).reset_index(drop = True).Topics[0])

In [42]:
# Train model
nnmf_model_speeches = Nmf(corpus=corpus_speeches_nnmf,
                                 id2word=id2word_speeches_nnmf,
                                 num_topics=k_optimal_nnmf_speeches,
                                 random_state=42)

In [43]:
# Calculate final coherence value
coherence_model_nnmf_speeches = CoherenceModel(model=nnmf_model_speeches, texts=texts_speeches_nnmf, dictionary=id2word_speeches_nnmf,
                                                    coherence='c_v')
coherence_nnmf_speeches = coherence_model_nnmf_speeches.get_coherence()
print("The final model coherence of the NNMF for Speeches is: " + str(round(coherence_nnmf_speeches,2)))

The final model coherence of the NNMF for Speeches is: 0.33


In [44]:
# Visually inspect result
nnmf_model_speeches.show_topics()

[(1,
  '0.046*"schnellen" + 0.043*"fall" + 0.040*"unternehmen" + 0.034*"sichern" + 0.013*"diskussion" + 0.012*"tweet" + 0.012*"klar" + 0.010*"falsch" + 0.008*"dringen" + 0.008*"herr"'),
 (9,
  '0.283*"mal" + 0.008*"lesen" + 0.008*"schauen" + 0.006*"schau" + 0.005*"tweet" + 0.004*"rein" + 0.004*"reden" + 0.004*"ne" + 0.003*"eigentlich" + 0.003*"letzt"'),
 (75,
  '0.088*"schön" + 0.060*"neu" + 0.023*"gesellschaft" + 0.023*"schritt" + 0.018*"bekommen" + 0.013*"kämpfen" + 0.010*"wünsche" + 0.008*"bauen" + 0.007*"alt" + 0.007*"richtung"'),
 (5,
  '0.121*"stellen" + 0.064*"handeln" + 0.053*"denken" + 0.016*"antrag" + 0.006*"wettbewerb" + 0.005*"fair" + 0.005*"falsch" + 0.005*"verfügung" + 0.004*"dar" + 0.004*"entgegen"'),
 (36,
  '0.086*"vorschlag" + 0.058*"liegen" + 0.048*"hoch" + 0.030*"helfen" + 0.026*"bringen" + 0.015*"gesellschaft" + 0.010*"zahl" + 0.007*"einkommen" + 0.007*"wert" + 0.007*"steuer"'),
 (22,
  '0.246*"europa" + 0.009*"sozial" + 0.007*"friede" + 0.006*"stellen" + 0.006*"gr

### 3.5.3 Bertopic

The last model we apply is [BERTopic](https://doi.org/10.5281/zenodo.4381785), which employs BERT transformers model and c-TF-IDF for creating topic models. This model architecture is pretty new and there is not much existing research on the topic. However first results seem promising.

We do not perform hyperparameter optimization for the BERTopic models, as we are having only limited computational power and the runtime of BERTopic is high.

In [45]:
def calculate_coherence_bert(topic_model, docs, topics):
    cleaned_docs = topic_model._preprocess_text(docs)

    # Extract vectorizer and tokenizer from BERTopic
    vectorizer = topic_model.vectorizer_model
    tokenizer = vectorizer.build_tokenizer()

    # Extract features for Topic Coherence evaluation
    words = vectorizer.get_feature_names()
    tokens = [tokenizer(doc) for doc in cleaned_docs]
    dictionary = corpora.Dictionary(tokens)
    corpus = [dictionary.doc2bow(token) for token in tokens]
    topic_words = [[words for words, _ in topic_model.get_topic(topic)] 
                   for topic in range(len(set(topics))-1)]

    # Evaluate
    coherence_model = CoherenceModel(topics=topic_words, 
                                     texts=tokens, 
                                     corpus=corpus,
                                     dictionary=dictionary, 
                                     coherence='c_v')
    coherence = coherence_model.get_coherence()
    return coherence

In [46]:
def assign_topic(topic_id, topic_model):
    return topic_model.get_topic_info(topic_id).Name.values[0]

#### 3.5.3.1 Compute BERTopic model Tweets

In [47]:
# Load data
tweets_processed_bert = pickle.load(open( "../data/processed/tweets_processed.p", "rb" ))
docs_tweets_bert = tweets_processed_bert.text_preprocessed_sentence.tolist()

In [48]:
# Prepare topic model 
topic_model_tweets = BERTopic(language="german", nr_topics="auto", calculate_probabilities = True, verbose = True)

In [49]:
# Compute Bertopic model
# Uncomment if you want to retrain the network
# start_time_bert_tweets = datetime.now()
# topics_tweets_bert, probs_tweets_bert = topic_model_tweets.fit_transform(docs_tweets_bert)
# end_time_bert_tweets = datetime.now()
# print('Duration: {}'.format(end_time_bert_tweets - start_time_bert_tweets))

In [50]:
# Calculate coherence
# Uncomment if you want to retrain the network
# coherence_bert_tweets = calculate_coherence_bert(topic_model_tweets,docs_tweets_bert, topics_tweets_bert)
# coherence_bert_tweets

In [51]:
# Visualise results
# Uncomment if you want to retrain the network
# topic_model_tweets.visualize_topics()

Based on first analyses we saw that there are too many topics, so we reduce the number of topics with the inherent reduction logic.

In [52]:
# Reduce topics
# Uncomment if you want to retrain the network
# topics_tweets_bert_reduced, probs_tweets_bert_reduced = topic_model_tweets.reduce_topics(docs_tweets_bert,
#                                                                                         topics_tweets_bert,
#                                                                                         probs_tweets_bert,
#                                                                                         nr_topics=25)

In [53]:
# Load model
# Comment out if you retrain the model
with open('../data/processed/topics_tweets_bert.pickle', 'rb') as handle:
    topics_tweets_bert_reduced = pickle.load(handle)
topic_model_tweets = BERTopic.load("../models/bertopic_tweets")

In [54]:
# Visualise results
topic_model_tweets.visualize_topics()

OMP: Info #271: omp_set_nested routine deprecated, please use omp_set_max_active_levels instead.


/Users/jakob/opt/miniconda3/envs/amca/lib/python3.8/site-packages/plotly/io/_renderers.py:396: DeprecationWarning:

distutils Version classes are deprecated. Use packaging.version instead.

/Users/jakob/opt/miniconda3/envs/amca/lib/python3.8/site-packages/plotly/io/_renderers.py:396: DeprecationWarning:

distutils Version classes are deprecated. Use packaging.version instead.



In [55]:
# Calculate coherence reduced
coherence_bert_tweets_reduced = calculate_coherence_bert(topic_model_tweets, docs_tweets_bert, 
                                                         topics_tweets_bert_reduced)
print("The final model coherence of the BERTopic for Tweets is: " + str(round(coherence_bert_tweets_reduced,2)))

The final model coherence of the BERTopic for Tweets is: 0.51


In [56]:
# Assign results to dataframe
tweets_processed_bert["topic_id"] = topics_tweets_bert_reduced
tweets_processed_bert["topic"] = tweets_processed_bert.topic_id.progress_apply(assign_topic,                                                                                    topic_model = topic_model_tweets)

  0%|          | 0/148312 [00:00<?, ?it/s]

In [57]:
# Save model and results
# Uncomment if you want to retrain the network
# topic_model_tweets.save("../models/bertopic_tweets")
# with open( "../data/processed/tweets_processed_bert.pickle", "wb" ) as handle:
#    pickle.dump(tweets_processed_bert, handle, protocol=pickle.HIGHEST_PROTOCOL)
# with open('../data/processed/probabilities_tweets_bert.pickle', 'wb') as handle:
#     pickle.dump(probs_tweets_bert_reduced, handle, protocol=pickle.HIGHEST_PROTOCOL)
# with open('../data/processed/topics_tweets_bert.pickle', 'wb') as handle:
#    pickle.dump(topics_tweets_bert_reduced, handle, protocol=pickle.HIGHEST_PROTOCOL)

#### 3.5.3.2 Compute BERTopic model Speeches

In [58]:
# Load data
speeches_processed_bert = pickle.load(open( "../data/processed/speeches_processed.p", "rb" ))
docs_speeches_bert = speeches_processed_bert.text_preprocessed_infrequent_sentence.tolist()

In [59]:
# Prepare topic model 
topic_model_speeches = BERTopic(language="german", nr_topics="auto", calculate_probabilities = True, 
                                verbose = True)

In [60]:
# Compute Bertopic mode
# Uncomment if you want to retrain the network
# start_time_bert_speeches = datetime.now()
# topics_speeches_bert, probs_speeches_bert = topic_model_speeches.fit_transform(docs_speeches_bert)
# end_time_bert_speeches = datetime.now()
# print('Duration: {}'.format(end_time_bert_speeches - start_time_bert_speeches))

In [61]:
# Load model
# Comment out if you retrain the model
with open('../data/processed/topics_speeches_bert.pickle', 'rb') as handle:
    topics_speeches_bert = pickle.load(handle)
topic_model_speeches = BERTopic.load("../models/bertopic_speeches")

In [62]:
# Visualise results
# Uncomment if you want to retrain the network
topic_model_speeches.visualize_topics()

/Users/jakob/opt/miniconda3/envs/amca/lib/python3.8/site-packages/plotly/io/_renderers.py:396: DeprecationWarning:

distutils Version classes are deprecated. Use packaging.version instead.

/Users/jakob/opt/miniconda3/envs/amca/lib/python3.8/site-packages/plotly/io/_renderers.py:396: DeprecationWarning:

distutils Version classes are deprecated. Use packaging.version instead.



In [63]:
# Calculate coherence reduced
coherence_bert_speeches = calculate_coherence_bert(topic_model_speeches, docs_speeches_bert, 
                                                         topics_speeches_bert)
print("The final model coherence of the BERTopic for speeches is: " + str(round(coherence_bert_speeches,2)))

The final model coherence of the BERTopic for speeches is: 0.6


In [64]:
# Assign results to dataframe
# Uncomment if you want to retrain the network
# speeches_processed_bert["topic_id"] = topics_speeches_bert
# speeches_processed_bert["topic"] = speeches_processed_bert.topic_id.progress_apply(assign_topic, 
#                                                                                   topic_model = topic_model_speeches)

In [65]:
# Save model and results
# Uncomment if you want to retrain the network
# topic_model_speeches.save("../models/bertopic_speeches")
# with open( "../data/processed/speeches_processed_bert.pickle", "wb" ) as handle:
#    pickle.dump(speeches_processed_bert, handle, protocol=pickle.HIGHEST_PROTOCOL)
# with open('../data/processed/probabilities_speeches_bert.pickle', 'wb') as handle:
#    pickle.dump(probs_speeches_bert, handle, protocol=pickle.HIGHEST_PROTOCOL)
# with open('../data/processed/topics_speeches_bert.pickle', 'wb') as handle:
#    pickle.dump(topics_speeches_bert, handle, protocol=pickle.HIGHEST_PROTOCOL)

### 3.5.4 Model selection

For the final model selection we evaluate the model based on the coherence and the visual inspection of the model results.

In [67]:
print("The final model coherence of the LDA for tweets is: " + str(round(coherence_lda_tweets,2)))
print("The final model coherence of the NNMF for tweets is: " + str(round(coherence_nnmf_tweets,2)))
print("The final model coherence of the BERTopic for tweets is: " + str(round(coherence_bert_tweets_reduced,2)))
print("The final model coherence of the LDA for speeches is: " + str(round(coherence_lda_speeches,2)))
print("The final model coherence of the NNMF for speeches is: " + str(round(coherence_nnmf_speeches,2)))
print("The final model coherence of the BERTopic for speeches is: " + str(round(coherence_bert_speeches,2)))

The final model coherence of the LDA for tweets is: 0.54
The final model coherence of the NNMF for tweets is: 0.33
The final model coherence of the BERTopic for tweets is: 0.51
The final model coherence of the LDA for speeches is: 0.37
The final model coherence of the NNMF for speeches is: 0.33
The final model coherence of the BERTopic for speeches is: 0.6


 NNMF models did not perform very well in terms of coherence, while the LDA model only showed good coherence values for the tweets dataset. BERTopic could perform well for both datasets in term of cohersion. Based on the visual inspection we saw very good results for BERTopic and medium results for the other two model types. Based on these criteria we decide for the BERTopic model for both dataset to create the final topic model. In the next section we will analyse the results of BERTopic and validate the the selected models based on word and topic intrusion metrics.